# Machine Learning and Predictive Analytics
# Assignment 7

Name: Troy Zhongyi Zhang           
Netid: zhongyiz@uchicago.edu        

# Recurrent Neural Network & Classification: 

The objective is to detect the security breach by predicting suspicious access using an RNN model and the provided Logfile data.

Logfile data includes login information like LogID, Timestamp, Method, Path, Status Code, Source, Remote Address, User Agent etc. The last indicator in each row denotes breach(1) and no breach(0) which is the target variable.

The expectation is that you will use the keras package to solve this problem (https://keras.io/). 

Data for HW: dev-access.csv

# 1. Data Processing:          
This data set is a bit messy, so the preprocessing portion is largely a tutorial to make sure students have data ready for keras. 

In [78]:
#!pip install keras
#!pip install tensorflow

In [79]:
#part 1-(a)
import sys
import os
import json
import pandas
import numpy
import optparse

from keras.callbacks import TensorBoard
from keras.models import Sequential, load_model
from keras.layers import LSTM, Dense, Dropout
from keras.layers.embeddings import Embedding
from keras.preprocessing import sequence
from keras.preprocessing.text import Tokenizer
from collections import OrderedDict

In [80]:
#part 1-(b)
dataframe = pandas.read_csv("dev-access.csv", engine='python', quotechar='|', header=None)

In [81]:
#part 1-(c)
dataset = dataframe.values

In [82]:
#part 1-(d)
dataset.shape

(26773, 2)

In [83]:
#part 1-(e)
X = dataset[:,0]

In [84]:
#part 1-(f)
Y = dataset[:,1]

In [85]:
#import pandas as pd
#X=pd.DataFrame(X)
X.shape

(26773,)

In [89]:
X

[[26,
  1,
  3,
  18,
  23,
  2,
  7,
  3,
  6,
  23,
  13,
  1,
  5,
  29,
  35,
  17,
  22,
  36,
  34,
  25,
  30,
  17,
  22,
  25,
  30,
  36,
  10,
  1,
  23,
  2,
  3,
  14,
  4,
  15,
  1,
  5,
  1,
  13,
  4,
  7,
  3,
  1,
  10,
  1,
  24,
  16,
  2,
  9,
  32,
  1,
  5,
  26,
  27,
  10,
  1,
  13,
  6,
  3,
  14,
  1,
  5,
  1,
  20,
  12,
  4,
  21,
  18,
  11,
  1,
  10,
  1,
  7,
  3,
  6,
  3,
  16,
  7,
  8,
  4,
  15,
  2,
  1,
  5,
  30,
  17,
  29,
  10,
  1,
  7,
  4,
  16,
  9,
  8,
  2,
  1,
  5,
  26,
  1,
  9,
  2,
  23,
  4,
  3,
  2,
  6,
  15,
  15,
  9,
  2,
  7,
  7,
  1,
  5,
  1,
  25,
  25,
  28,
  29,
  30,
  29,
  28,
  29,
  29,
  34,
  28,
  22,
  34,
  36,
  1,
  10,
  1,
  9,
  2,
  33,
  2,
  9,
  2,
  9,
  1,
  5,
  1,
  14,
  3,
  3,
  13,
  5,
  20,
  20,
  12,
  4,
  8,
  6,
  12,
  14,
  4,
  7,
  3,
  5,
  25,
  17,
  17,
  22,
  20,
  2,
  11,
  3,
  2,
  9,
  1,
  27,
  10,
  1,
  9,
  4,
  16,
  3,
  2,
  1,
  5,
  1,
  20,
  12,
  4,
  

In [48]:
#part 1-(g)
for index, item in enumerate(X):
    # Quick hack to space out json elements
    reqJson = json.loads(item, object_pairs_hook=OrderedDict)
    del reqJson['timestamp']
    del reqJson['headers']
    del reqJson['source']
    del reqJson['route']
    del reqJson['responsePayload']
    X[index] = json.dumps(reqJson, separators=(',', ':'))

In [88]:
#part 1-(h)
tokenizer = Tokenizer(filters='\t\n', char_level=True)
tokenizer.fit_on_texts(X)

# we will need this later
num_words = len(tokenizer.word_index)+1
X = tokenizer.texts_to_sequences(X)

In [74]:
num_words

64

In [76]:
tokenizer.word_index

{'"': 1,
 'e': 2,
 't': 3,
 'o': 4,
 ':': 5,
 'a': 6,
 's': 7,
 'c': 8,
 'r': 9,
 ',': 10,
 'n': 11,
 'l': 12,
 'p': 13,
 'h': 14,
 'd': 15,
 'u': 16,
 '0': 17,
 'i': 18,
 '-': 19,
 '/': 20,
 'g': 21,
 '2': 22,
 'm': 23,
 'q': 24,
 '8': 25,
 '{': 26,
 '}': 27,
 '.': 28,
 '1': 29,
 '4': 30,
 ' ': 31,
 'y': 32,
 'f': 33,
 '3': 34,
 '5': 35,
 '7': 36,
 '6': 37,
 '*': 38,
 ';': 39,
 '=': 40,
 'k': 41,
 'v': 42,
 '9': 43,
 'z': 44,
 'x': 45,
 'b': 46,
 'w': 47,
 '&': 48,
 'j': 49,
 "'": 50,
 '<': 51,
 '\\': 52,
 '>': 53,
 '_': 54,
 '!': 55,
 '(': 56,
 '#': 57,
 ')': 58,
 '?': 59,
 '[': 60,
 ']': 61,
 '+': 62,
 '‑': 63}

In [50]:
print(num_words)

62


In [51]:
#part 1-(i)
max_log_length = 1024
X_processed = sequence.pad_sequences(X, maxlen=max_log_length)

In [52]:
X_processed = pandas.DataFrame(X_processed)
Y = pandas.DataFrame(Y)
X_processed.shape

(26773, 1024)

In [53]:
Y.shape

(26773, 1)

In [54]:
#part 1-(j)
from sklearn.metrics import classification_report
from sklearn.model_selection import cross_val_score
import sklearn.model_selection as cv
from sklearn.model_selection import train_test_split

(X_train, X_test, y_train, y_test) = train_test_split(X_processed, Y, test_size=.25, random_state=42)

In [94]:
X_test.shape

(6694, 1024)

# 2. Model 1 - RNN:           
The first model will be a pretty minimal RNN with only an embedding layer, simple RNN and Dense layer. The next model we will add a few more layers. 

In [55]:
# 2-(a)
from keras.models import Sequential
from keras.layers import Dense, Activation

model = Sequential([Dense(32, input_shape=(784,)),
                    Activation('relu'),
                    Dense(10),
                    Activation('softmax'),])

W0825 20:47:23.295485 4791113152 deprecation_wrapper.py:119] From /Users/zhongyizhang/env/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:74: The name tf.get_default_graph is deprecated. Please use tf.compat.v1.get_default_graph instead.

W0825 20:47:23.310286 4791113152 deprecation_wrapper.py:119] From /Users/zhongyizhang/env/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:517: The name tf.placeholder is deprecated. Please use tf.compat.v1.placeholder instead.

W0825 20:47:23.312438 4791113152 deprecation_wrapper.py:119] From /Users/zhongyizhang/env/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:4138: The name tf.random_uniform is deprecated. Please use tf.random.uniform instead.



In [56]:
# 2-(b)
model = Sequential()
model.add(Embedding(num_words, 32, input_length=max_log_length))

In [57]:
# 2-(c)
from keras.layers import SimpleRNN
model.add(SimpleRNN(32,activation='relu'))

In [58]:
# 2-(d)
model.add(Dense(1, activation='sigmoid'))

In [59]:
# 2-(e)

# Params:
# - loss = binary_crossentropy
# - optimizer = adam
# - metrics = accuracy

model.compile(loss = 'binary_crossentropy', optimizer='adam', metrics = ['accuracy'])

W0825 20:47:25.158035 4791113152 deprecation_wrapper.py:119] From /Users/zhongyizhang/env/lib/python3.7/site-packages/keras/optimizers.py:790: The name tf.train.Optimizer is deprecated. Please use tf.compat.v1.train.Optimizer instead.

W0825 20:47:25.177924 4791113152 deprecation_wrapper.py:119] From /Users/zhongyizhang/env/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:3376: The name tf.log is deprecated. Please use tf.math.log instead.

W0825 20:47:25.182360 4791113152 deprecation.py:323] From /Users/zhongyizhang/env/lib/python3.7/site-packages/tensorflow/python/ops/nn_impl.py:180: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


In [60]:
# 2-(f)
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_1 (Embedding)      (None, 1024, 32)          1984      
_________________________________________________________________
simple_rnn_1 (SimpleRNN)     (None, 32)                2080      
_________________________________________________________________
dense_3 (Dense)              (None, 1)                 33        
Total params: 4,097
Trainable params: 4,097
Non-trainable params: 0
_________________________________________________________________


In [61]:
# 2-(g)
model.fit(X_train, y_train, epochs=3, batch_size=128)

W0825 20:47:28.031678 4791113152 deprecation_wrapper.py:119] From /Users/zhongyizhang/env/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:986: The name tf.assign_add is deprecated. Please use tf.compat.v1.assign_add instead.



Epoch 1/3


InvalidArgumentError: indices[83,996] = 62 is not in [0, 62)
	 [[{{node embedding_1/embedding_lookup}}]]

In [21]:
# 2-(h)
score = model.evaluate(X_test, y_test, batch_size=128)
print("\n loss value:",score[0], ",\n accuracy value:",score[1])

6694/6694 [==============================] - 2s 335us/step

 loss value: 0.0530328656557067 ,
 accuracy value: 0.9861069614580221


# 3) Model 2 - LSTM + Dropout Layers:
Now we will add a few new layers to our RNN and incorporate the more powerful LSTM. You will be creating a new model here, so make sure to call it something different than the model from Part 2.

In [22]:
# 3-(a)
from keras.layers import Dropout
from keras.layers import LSTM

model2 = Sequential([Dense(32, input_shape=(784,)),
                    Activation('relu'),
                    Dense(10),
                    Activation('softmax'),])
model2 = Sequential()
model2.add(Embedding(num_words, 32, input_length=max_log_length))
model2.add(LSTM(units = 64, recurrent_dropout = 0.5))
model2.add(Dropout(0.5))
model2.add(Dense(1, activation='sigmoid'))

W0822 02:03:08.049583 4518507968 deprecation.py:506] From /Users/zhongyizhang/env/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:3445: calling dropout (from tensorflow.python.ops.nn_ops) with keep_prob is deprecated and will be removed in a future version.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


In [23]:
# 3-(b)
model2.compile(loss = 'binary_crossentropy', optimizer='adam', metrics = ['accuracy'])

In [24]:
# 3-(c)
model2.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_2 (Embedding)      (None, 1024, 32)          2016      
_________________________________________________________________
lstm_1 (LSTM)                (None, 64)                24832     
_________________________________________________________________
dropout_1 (Dropout)          (None, 64)                0         
_________________________________________________________________
dense_6 (Dense)              (None, 1)                 65        
Total params: 26,913
Trainable params: 26,913
Non-trainable params: 0
_________________________________________________________________


In [25]:
# 3-(d)
model2.fit(X_train, y_train, epochs=3, batch_size=128)

Epoch 1/3
20079/20079 [==============================] - 122s 6ms/step - loss: 0.5474 - acc: 0.7135
Epoch 2/3
20079/20079 [==============================] - 122s 6ms/step - loss: 0.3024 - acc: 0.9021
Epoch 3/3
20079/20079 [==============================] - 130s 6ms/step - loss: 0.2048 - acc: 0.9502


In [26]:
# 3-(e)
score2 = model2.evaluate(X_test, y_test, batch_size=128)
print("\n loss value:",score2[0], ",\n accuracy value:",score2[1])

6694/6694 [==============================] - 6s 904us/step

 loss value: 0.15936755771966596 ,
 accuracy value: 0.9613086345981476


# 4) Recurrent Neural Net Model 3: Build Your Own
You wil now create your RNN based on what you have learned from Model 1 & Model 2:

In [27]:
X_train.shape

(20079, 1024)

In [29]:
import keras

In [30]:
# 4-(a)
model3 = Sequential([Dense(32, input_shape=(784,)),
                    Activation('relu'),
                    Dense(10),
                    Activation('softmax'),])
model3 = Sequential()
model3.add(Embedding(num_words, 32, input_length=max_log_length))
model3.add(LSTM(units = 64, recurrent_dropout = 0.5, return_sequences=True))
#model3.add(LSTM(64, return_sequences=True))
model3.add(LSTM(64)) 
model3.add(Dense(2, input_dim=2, activation=keras.activations.sigmoid, use_bias=True))
model3.add(Dense(1, activation='sigmoid'))

In [31]:
# 4-(b)
model3.compile(optimizer='rmsprop', loss='binary_crossentropy', metrics=['accuracy'])

In [32]:
# 4-(c)
model3.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_4 (Embedding)      (None, 1024, 32)          2016      
_________________________________________________________________
lstm_4 (LSTM)                (None, 1024, 64)          24832     
_________________________________________________________________
lstm_5 (LSTM)                (None, 64)                33024     
_________________________________________________________________
dense_11 (Dense)             (None, 2)                 130       
_________________________________________________________________
dense_12 (Dense)             (None, 1)                 3         
Total params: 60,005
Trainable params: 60,005
Non-trainable params: 0
_________________________________________________________________


In [33]:
# 4-(d)
model3.fit(X_train, y_train, epochs=3, batch_size=128)

Epoch 1/3
20079/20079 [==============================] - 239s 12ms/step - loss: 0.4944 - acc: 0.8060
Epoch 2/3
20079/20079 [==============================] - 242s 12ms/step - loss: 0.3770 - acc: 0.9061
Epoch 3/3
20079/20079 [==============================] - 237s 12ms/step - loss: 0.2904 - acc: 0.9571


In [34]:
# 4-(e)
score3 = model3.evaluate(X_test, y_test, batch_size=128)
print("\n loss value:",score3[0], ",\n accuracy value:",score3[1])

6694/6694 [==============================] - 11s 2ms/step

 loss value: 0.24630625485430058 ,
 accuracy value: 0.9805796235434717


# Conceptual Questions: 

5) Explain the difference between the relu activation function and the sigmoid activation function.

6) Describe what one epoch actually is (epoch was a parameter used in the .fit() method).

7) Explain how dropout works (you can look at the keras code and/or documentation) for (a) training, and (b) test data sets.

8) Explain why problems such as this homework assignment are better modeled with RNNs than CNNs. What type of problem will CNNs outperform RNNs on?

9) Explain what RNN problem is solved using LSTM and briefly describe how.

### Answers:

5) 
#### Sigmoid
The Sigmoid Function curve looks like a S-shape.           
Sigmoid: A(x) = 1/(1+e**(-x))          
Pros: it is differentiable, non-linear, produces non-binary activations and it is bounded between (0,1).        
Cons: vanishing gradients. Yes, the values are between 0 & 1 and it will be zero when value of the activation reaches 0 or 1 (the horizontal part of the curve).        

#### Relu
Relu: A(x) = max(0,x)         
Output is defined as A(x)
Relu has a range of [0 to infinity).                 
Pros: as it is clear from the figure that any varient of Relu doesn’t have a flat curve, it avoids vanishing gradient problem.             
Cons: it is not differentiable at 0 and may result in exploding gradients.  

6) The number of epochs is a hyperparameter that defines the number times that the learning algorithm will work through the entire training dataset. One epoch means that each sample in the training dataset has had an opportunity to update the internal model parameters. An epoch is comprised of one or more batches. One epoch is when an entire dataset is passed both forward and backward through the neural network only once. One epoch is too big to feed to the computer at once. So, we divide it in several smaller batches. For example: if I have 1000 training examples, and my batch size is 500, then it will take 2 iterations to complete 1 epoch.

The number of epochs is traditionally large, often hundreds or thousands, allowing the learning algorithm to run until the error from the model has been sufficiently minimized.

7) Dropout is a technique where randomly selected neurons are ignored during training. This means that their contribution to the activation of downstream neurons is temporally removed on the forward pass and any weight updates are not applied to the neuron on the backward pass. In Keras, dropout is easily implemented by randomly selecting nodes to be dropped-out with a given probability each weight update cycle. 
 
(a) Training: For each hidden layer, for each training sample, for each iteration, ignore (zero out) a random fraction, p, of nodes (and corresponding activations).          
(b) Testing: Use all activations, but reduce them by a factor p (to account for the missing activations during training).         

8) Because our dataset is a sequence prediction problems. While RNN works on the principle of saving the output of a layer and feeding this back to the input in order to predict the output of the layer. CNN considers only the current input while RNN considers the current input and also the previously received inputs. CNN can memorize previous inputs due to its internal memory.

CNNs are good with hierarchical or spatial data and extracting unlabeled features. Those could be images or written characters. CNN also did good jobs on image data, classification prediction problems, regression prediction problems, text data, time series data, and sequence input data. RNN is not at tabular data and image data. LSTM-RNN are very powerful when dealing with timeseries, simply because they can store information about previous values and exploit the time dependencies between the samples. However, according to some reports, RNNs and LSTMs have been tested on time series forecasting problems, but the results have been poor, to say the least. Anyway, CNN will outperform image data better than RNN for sure.

9) Long Short Term Memory networks – usually just called “LSTMs” – are a special kind of RNN, capable of learning long-term dependencies. LSTM networks solve the problem of vanishing gradients in a RNN. LSTMs solve the problem by creating a connection between the forget gate activations and the gradients computation, this connection creates a path for information flow through the forget gate for information the LSTM should not forget.

------------------